In [1]:
###### 调用相关库 #######
import tensorflow as tf
import numpy as np
import pandas as pd 
import matplotlib.pyplot as plt
import scipy.io
from scipy.interpolate import griddata
from pyDOE import lhs
#from plotting import newfig, savefig
from mpl_toolkits.mplot3d import Axes3D
import time
import matplotlib.gridspec as gridspec
from mpl_toolkits.axes_grid1 import make_axes_locatable
import os 
import warnings
warnings.filterwarnings('ignore')

os.environ['CUDA_VISIBLE_DEVICES'] = "0" 
np.random.seed(0)#12345,1234,12
tf.compat.v1.random.set_random_seed(0)

2025-02-28 00:10:55.016207: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcudart.so.11.0


In [2]:
class PhysicsInformedNN:
    it = 0
    
    # def __init__(self, X_u, u, X_f, layers,lb, ub,vf,rho_j,v_lb,v_ub,rho_lb,rho_ub):
    def __init__(self, X_u, u, X_f, layers,lb, ub,vf,rho_j):
        self.vf = vf
        self.rho_j = rho_j
        self.lb = lb
        self.ub = ub
        # self.v_lb = v_lb
        # self.v_ub = v_ub
        # self.rho_lb = rho_lb
        # self.rho_ub = rho_ub
    
        self.x_u = X_u[:,0:1]
        self.t_u = X_u[:,1:2]
        
        self.x_f = X_f[:,0:1]
        self.t_f = X_f[:,1:2]
        
        self.v = u[:,0:1]
        self.rho = u[:,1:2]
        
        self.layers = layers
        self.weights, self.biases = self.initialize_NN(layers)
        
        self.sess = tf.compat.v1.Session(config=tf.compat.v1.ConfigProto(allow_soft_placement=True,
                                                     log_device_placement=True))
        
        self.x_u_tf = tf.placeholder(tf.float32, shape=[None, self.x_u.shape[1]])
        self.t_u_tf = tf.placeholder(tf.float32, shape=[None, self.t_u.shape[1]])        
        self.v_tf = tf.placeholder(tf.float32, shape=[None, self.v.shape[1]])
        self.rho_tf = tf.placeholder(tf.float32, shape=[None, self.rho.shape[1]])
        self.x_f_tf = tf.placeholder(tf.float32, shape=[None, self.x_f.shape[1]])
        self.t_f_tf = tf.placeholder(tf.float32, shape=[None, self.t_f.shape[1]])        
                
        self.v_pred, self.rho_pred = self.net_u(self.x_u_tf, self.t_u_tf) 
        self.f_pde, self.f_fd, self.f_loss = self.net_f(self.x_f_tf, self.t_f_tf) 
        
        self.loss = 1 * tf.reduce_mean(tf.square(self.v_tf - self.v_pred)) +  1 * tf.reduce_mean(tf.square(self.rho_tf - self.rho_pred)) +\
                       0.2 * tf.reduce_mean(tf.square(self.f_pde)) + 0.2 *  tf.reduce_mean(tf.square(self.f_fd))+ 0.1 *  tf.reduce_mean(tf.square(self.f_loss))
                         
        self.optimizer = tf.contrib.opt.ScipyOptimizerInterface(self.loss, 
                                                                method = 'L-BFGS-B', 
                                                                options = {'maxiter': 50000,
                                                                           'maxfun': 50000,
                                                                           'maxcor': 50,
                                                                           'maxls': 50,
                                                                           'ftol' : 1.0 * np.finfo(float).eps})
        
        self.optimizer_Adam = tf.compat.v1.train.AdamOptimizer(0.001)
        self.train_op_Adam = self.optimizer_Adam.minimize(self.loss)
        
        init = tf.compat.v1.global_variables_initializer()
        self.sess.run(init)

    def initialize_NN(self, layers):  
        
        weights = []
        biases = []
        num_layers = len(layers) 
        for l in range(0, num_layers-1):
            W = self.xavier_init(size=[layers[l], layers[l+1]])
            b = tf.Variable(tf.zeros([1,layers[l+1]], dtype=tf.float32), dtype=tf.float32)
            weights.append(W)
            biases.append(b)
        return weights, biases
        
    def xavier_init(self, size):
        in_dim = size[0]
        out_dim = size[1]        
        xavier_stddev = np.sqrt(2/(in_dim + out_dim))
        return tf.Variable(tf.random.truncated_normal([in_dim, out_dim], stddev=xavier_stddev), dtype=tf.float32)
    
    def neural_net(self, X, weights, biases):
        
        num_layers = len(weights) + 1
        H = 2.0*(X - self.lb)/(self.ub - self.lb) - 1.0         # scaling
        for l in range(0,num_layers-2):
            W = weights[l]
            b = biases[l]
            H = tf.tanh(tf.add(tf.matmul(H, W), b))
        W = weights[-1]
        b = biases[-1]
        Y = tf.add(tf.matmul(H, W), b)
        
        return Y
            
    def net_u(self, x, t):
        
        u = self.neural_net(tf.concat([x,t],1), self.weights, self.biases)
        v = u[:,0:1]
        rho = u[:,1:2]
        return v,rho
    
    def net_f(self, x,t):
        v,rho = self.net_u(x,t)
        # v = v * (v_ub-v_lb) + v_lb
        # rho = rho * (rho_ub-rho_lb) + rho_lb
        rho_t = tf.gradients(rho, t)[0] 
        rho_x = tf.gradients(rho, x)[0]
        v_x = tf.gradients(v, x)[0]
        f_pde = rho_t + rho * v_x + v * rho_x       #LWR的loss
        f_fd = self.vf * tf.exp(-rho/self.rho_j)-v  #基本图loss
        
        fd = self.vf * tf.exp(-rho/self.rho_j)     
        f_pde_2 = v + vf- fd     
        f_pde_3 = fd - v
        f_pde_2_t = tf.gradients(f_pde_2, t)[0]    
        f_pde_2_x = tf.gradients(f_pde_2, x)[0] 
        f_loss = f_pde_2_t + v * f_pde_2_x - (f_pde_3)/30   #二阶ARZ
        return f_pde, f_fd, f_loss

    
    def callback(self, loss):
        print('Loss:', loss)
        
    def train(self,nIter):     
        
        tf_dict = {self.x_u_tf: self.x_u, self.t_u_tf: self.t_u, self.v_tf: self.v,self.rho_tf: self.rho,
                   self.x_f_tf: self.x_f, self.t_f_tf: self.t_f}   
        
        start_time = time.time()
        MSE_history=[]
        for it in range(nIter):
            self.sess.run(self.train_op_Adam, tf_dict)
            if it %100 == 0:
#                elapsed = time.time() - start_time
                loss_value = self.sess.run(self.loss, tf_dict)
                print('It: %d, Loss: %.3e' % 
                      (it, loss_value))
#                start_time = time.time()
                MSE_history.append(loss_value)
        self.optimizer.minimize(self.sess, 
                                feed_dict = tf_dict,         
                                fetches = [self.loss], 
                                loss_callback = self.callback)        
        return MSE_history
    
    def predict(self, X_star):      
  
        v_star = self.sess.run(self.v_pred, {self.x_u_tf: X_star[:,0:1], self.t_u_tf: X_star[:,1:2]})  
        rho_star = self.sess.run(self.rho_pred, {self.x_u_tf: X_star[:,0:1], self.t_u_tf: X_star[:,1:2]})  
                
        f_v_star = self.sess.run(self.f_pde, {self.x_f_tf: X_star[:,0:1], self.t_f_tf: X_star[:,1:2]})
        f_rho_star = self.sess.run(self.f_fd, {self.x_f_tf: X_star[:,0:1], self.t_f_tf: X_star[:,1:2]})
        
        return v_star, rho_star

In [ ]:
if __name__ == "__main__": 
    layers = [2, 128, 128, 128, 128, 128, 128, 128, 128, 128, 2] #######
    data_tokyo = pd.read_csv("holiday_7days.csv")
    data_tokyo = data_tokyo.iloc[:288*3*23,:]
    data_tokyo['distance'] = data_tokyo['distance'].replace(0, 1)
    density = data_tokyo['flow']/data_tokyo['speed']
    data_tokyo['density'] = density
    flat_arrayv = data_tokyo['speed'].values.flatten()
    flat_arrayrho = data_tokyo['density'].values.flatten()
    print(flat_arrayv)
    rx = data_tokyo.iloc[:23,1]
    rt = np.linspace(0.083, 24*3, 288*3)
    print(len(rt))
    x_mesh, t_mesh = np.meshgrid(rx, rt)
    X_star = np.concatenate((np.expand_dims(x_mesh, -1), np.expand_dims(t_mesh, -1)), axis=-1)
    X_star = X_star.reshape(-1, 2) 
    print(X_star)
    lb = X_star.min(0)
    ub = X_star.max(0)
    test = data_tokyo.loc[:,['speed','density']]
    test = np.array(test.iloc[:,:])
    
    # ------------------- 测试不同线圈的效果，每次运行需要手动选择线圈数量 ---------------------
    # loopidx = [0,7,14,22] # 4/23
    # loopidx = [0,3,7,10,16,22] # 6/23
    # loopidx = [0,1,3,5,7,12,16,22] # 8/23
    # loopidx = [0,1,3,5,7,10,12,16,18,22] # 10/23
    loopidx = [0,3,5,7,9,10,12,14,16,18,20,22] # 12/23
    # --------------------------------------------------------------------------------------
    
    span = np.array(loopidx)
    X_u_train = np.hstack([np.meshgrid(rx[span], rt)[0].reshape(-1, 1), np.meshgrid(rx[span], rt)[1].reshape(-1, 1)]) # 训练集 (x,t)
    u_train = data_tokyo[data_tokyo['distance'].isin(data_tokyo.loc[span,:]['distance'])].loc[:,['speed','density']]
    u_train = np.array(u_train.iloc[:,:])
    idx2 = np.random.choice(X_star.shape[0], int(X_star.shape[0] * 0.6), replace=False)
    X_f_train = X_star[idx2,:]
    X_u_train = X_u_train[:, :]
    u_train = u_train[:,:]
    u_lb = u_train.min(0)
    u_ub = u_train.max(0)
    print(u_train)
    u_train = (u_train-u_lb)/(u_ub-u_lb)
    print(X_u_train)
    print(u_train)
    print(X_f_train.shape)
    
    # ---------------- 无循环版本，需要从0。01-0.99依次打开注释，并运行保存文件 -----------------------
    # ------------- alpha = 0.01 --------------
    # vf = (110.49 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (43.56- u_lb[1]) / (u_ub[1]-u_lb[1])
    # ------------- alpha = 0.08 --------------
    # vf = (103.64 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (42.78- u_lb[1]) / (u_ub[1]-u_lb[1])
     # ------------- alpha = 0.15 --------------
    # vf = (100.66 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (42.43- u_lb[1]) / (u_ub[1]-u_lb[1])
     # ------------- alpha = 0.22 --------------
    # vf = (98.52 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (42.15- u_lb[1]) / (u_ub[1]-u_lb[1])
     # ------------- alpha = 0.29 --------------
    # vf = (96.76 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (41.91- u_lb[1]) / (u_ub[1]-u_lb[1])
    # ------------- alpha = 0.36 --------------
    # vf = (95.18 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (41.72- u_lb[1]) / (u_ub[1]-u_lb[1])
    # ------------- alpha = 0.43 --------------
    # vf = (93.71 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (41.53- u_lb[1]) / (u_ub[1]-u_lb[1])
    # ------------- alpha = 0.50 --------------
    # vf = (92.28 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (41.35- u_lb[1]) / (u_ub[1]-u_lb[1])
    # ------------- alpha = 0.57 --------------
    # vf = (90.84 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (41.17- u_lb[1]) / (u_ub[1]-u_lb[1])
    # # ------------- alpha = 0.64 --------------
    # vf = (89.32 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (40.97- u_lb[1]) / (u_ub[1]-u_lb[1])
    # ------------- alpha = 0.71 --------------
    # vf = (87.63 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (40.77- u_lb[1]) / (u_ub[1]-u_lb[1])
    # ------------- alpha = 0.78 --------------
    # vf = (85.65 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (40.53- u_lb[1]) / (u_ub[1]-u_lb[1])
    # ------------- alpha = 0.85 --------------
    # vf = (83.10- u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (40.25- u_lb[1]) / (u_ub[1]-u_lb[1])
    # ------------- alpha = 0.92 -------------
    # vf = (79.30 - u_lb[0]) / (u_ub[0]-u_lb[0])
    # rho_j = (39.80- u_lb[1]) / (u_ub[1]-u_lb[1])
    # ------------- alpha = 0.99 --------------
    
#     vf = (70.49 - u_lb[0]) / (u_ub[0]-u_lb[0])
#     rho_j = (37.64- u_lb[1]) / (u_ub[1]-u_lb[1])

#     model = PhysicsInformedNN(X_u_train, u_train, X_f_train, layers,lb, ub,vf,rho_j)
#     start_time = time.time()                
#     model.train(20000)
#     elapsed = time.time() - start_time                
#     print('Training time: %.4f' % (elapsed))
#     v_pred, rho_pred = model.predict(X_star)
#     v_pred = v_pred * (u_ub[0]-u_lb[0])+u_lb[0]
#     rho_pred = rho_pred * (u_ub[1]-u_lb[1])+u_lb[1]

#     path= r'/root/autodl-tmp/12loops'
#     import os
#     np.save(os.path.join(path,'v_alpha'+ str(0.99) + '_loop12' + '.npy'),arr=v_pred)#######
#     np.save(os.path.join(path,'rho_alpha'+ str(0.99) + '_loop12'+ '.npy'),arr=rho_pred)#######
# ----------------------------------------------------------------------------------------------------

# ------------------- 循环版，遍历每个alpha，运行模型并保持结果 ------------
    # 定义不同alpha对应的参数值
    alpha_params = [
        (0.01, 110.49, 43.56),
        (0.08, 103.64, 42.78),
        (0.15, 100.66, 42.43),
        (0.22, 98.52, 42.15),
        (0.29, 96.76, 41.91),
        (0.36, 95.18, 41.72),
        (0.43, 93.71, 41.53),
        (0.50, 92.28, 41.35),
        (0.57, 90.84, 41.17),
        (0.64, 89.32, 40.97),
        (0.71, 87.63, 40.77),
        (0.78, 85.65, 40.53),
        (0.85, 83.10, 40.25),
        (0.92, 79.30, 39.80),
        (0.99, 70.49, 37.64)
    ]

    for idx, (alpha, vf_num, rho_num) in enumerate(alpha_params):

        print(f"\n正在处理 alpha={alpha:.2f} ({idx+1}/{len(alpha_params)})")

        # 计算归一化参数
        vf = (vf_num - u_lb[0]) / (u_ub[0] - u_lb[0])
        rho_j = (rho_num - u_lb[1]) / (u_ub[1] - u_lb[1])

        # 创建并训练模型
        model = PhysicsInformedNN(X_u_train, u_train, X_f_train, layers, lb, ub, vf, rho_j)
        start_time = time.time()
        model.train(20000)
        elapsed = time.time() - start_time
        print(f'Training time: {elapsed:.4f}s')

        # 预测并反归一化
        v_pred, rho_pred = model.predict(X_star)
        v_pred = v_pred * (u_ub[0] - u_lb[0]) + u_lb[0]
        rho_pred = rho_pred * (u_ub[1] - u_lb[1]) + u_lb[1]

        # # 保存结果
        path = r'/root/autodl-tmp/12loops'
        np.save(os.path.join(path, f'v_alpha{alpha:.2f}_loop12.npy'), v_pred)
        np.save(os.path.join(path, f'rho_alpha{alpha:.2f}_loop12.npy'), rho_pred)

        # 新增完成提示 ---------------------------------------------------------------
        print(f"√ 已完成 alpha={alpha:.2f} 的运算")
        # ---------------------------------------------------------------------------

[63.7 66.3 63.1 ... 79.2 78.7 75.3]
864
[[1.000e+00 8.300e-02]
 [5.700e+02 8.300e-02]
 [1.290e+03 8.300e-02]
 ...
 [1.126e+04 7.200e+01]
 [1.203e+04 7.200e+01]
 [1.278e+04 7.200e+01]]
[[63.7         4.42700157]
 [79.4         6.04534005]
 [81.9         4.24908425]
 ...
 [72.3         8.04979253]
 [79.2         7.04545455]
 [75.3         7.72908367]]
[[1.000e+00 8.300e-02]
 [1.590e+03 8.300e-02]
 [2.910e+03 8.300e-02]
 ...
 [1.025e+04 7.200e+01]
 [1.126e+04 7.200e+01]
 [1.278e+04 7.200e+01]]
[[0.64965986 0.03999428]
 [0.8276644  0.05670003]
 [0.85600907 0.03815767]
 ...
 [0.74716553 0.07739156]
 [0.82539683 0.067024  ]
 [0.78117914 0.07408095]]
(11923, 2)

正在处理 alpha=0.01 (1/15)


2025-02-28 00:10:57.754332: I tensorflow/core/platform/cpu_feature_guard.cc:145] Your CPU supports instructions that this TensorFlow binary was not compiled to use: SSE4.1 SSE4.2 AVX
2025-02-28 00:10:57.786129: I tensorflow/core/platform/profile_utils/cpu_utils.cc:94] CPU Frequency: 2400000000 Hz
2025-02-28 00:10:57.790104: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x556de2c1b860 initialized for platform Host (this does not guarantee that XLA will be used). Devices:
2025-02-28 00:10:57.790139: I tensorflow/compiler/xla/service/service.cc:176]   StreamExecutor device (0): Host, Default Version
2025-02-28 00:10:57.793129: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcuda.so.1
2025-02-28 00:10:57.850242: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1666] Found device 0 with properties: 
name: NVIDIA GeForce RTX 3080 Ti major: 8 minor: 6 memoryClockRate(GHz): 1.665
pciBusID: 0000:d9:00.0
2025-02-28 00:10:57

Device mapping:
/job:localhost/replica:0/task:0/device:XLA_CPU:0 -> device: XLA_CPU device
/job:localhost/replica:0/task:0/device:GPU:0 -> device: 0, name: NVIDIA GeForce RTX 3080 Ti, pci bus id: 0000:d9:00.0, compute capability: 8.6
/job:localhost/replica:0/task:0/device:XLA_GPU:0 -> device: XLA_GPU device




2025-02-28 00:10:58.850395: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1206] Device interconnect StreamExecutor with strength 1 edge matrix:
2025-02-28 00:10:58.850432: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1212]      0 
2025-02-28 00:10:58.850440: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1225] 0:   N 
2025-02-28 00:10:58.851971: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1351] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 9871 MB memory) -> physical GPU (device: 0, name: NVIDIA GeForce RTX 3080 Ti, pci bus id: 0000:d9:00.0, compute capability: 8.6)
2025-02-28 00:10:58.856560: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x556e0a38a150 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2025-02-28 00:10:58.856578: I tensorflow/compiler/xla/service/service.cc:176]   StreamExecutor device (0): NVIDIA GeForce RTX 3080 Ti, Compute Capability 8.6



The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.



...

Training time: 451.6751s
√ 已完成 alpha=0.01 的运算

正在处理 alpha=0.08 (2/15)
Device mapping:
/job:localhost/replica:0/task:0/device:XLA_CPU:0 -> device: XLA_CPU device
/job:localhost/replica:0/task:0/device:GPU:0 -> device: 0, name: NVIDIA GeForce RTX 3080 Ti, pci bus id: 0000:d9:00.0, compute capability: 8.6
/job:localhost/replica:0/task:0/device:XLA_GPU:0 -> device: XLA_GPU device



2025-02-28 00:18:38.832157: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1666] Found device 0 with properties: 
name: NVIDIA GeForce RTX 3080 Ti major: 8 minor: 6 memoryClockRate(GHz): 1.665
pciBusID: 0000:d9:00.0
2025-02-28 00:18:38.832377: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcudart.so.11.0
2025-02-28 00:18:38.832577: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcublas.so.11
2025-02-28 00:18:38.832604: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcufft.so.10
2025-02-28 00:18:38.832625: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcurand.so.10
2025-02-28 00:18:38.832648: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcusolver.so.11
2025-02-28 00:18:38.832663: I tensorflow/stream_executor/

1/Adam/Initializer/zeros: (Const): /job:localhost/replica:0/task:0/device:GPU:0
Variable_11/Adam_1/Initializer/zeros: (Const): /job:localhost/replica:0/task:0/device:GPU:0
Variable_12/Adam/Initializer/zeros/shape_as_tensor: (Const): /job:localhost/replica:0/task:0/device:GPU:0
Variable_12/Adam/Initializer/zeros/Const: (Const): /job:localhost/replica:0/task:0/device:GPU:0
Variable_12/Adam_1/Initializer/zeros/shape_as_tensor: (Const): /job:localhost/replica:0/task:0/device:GPU:0
Variable_12/Adam_1/Initializer/zeros/Const: (Const): /job:localhost/replica:0/task:0/device:GPU:0
Variable_13/Adam/Initializer/zeros: (Const): /job:localhost/replica:0/task:0/device:GPU:0
Variable_13/Adam_1/Initializer/zeros: (Const): /job:localhost/replica:0/task:0/device:GPU:0
Variable_14/Adam/Initializer/zeros/shape_as_tensor: (Const): /job:localhost/replica:0/task:0/device:GPU:0
Variable_14/Adam/Initializer/zeros/Const: (Const): /job:localhost/replica:0/task:0/device:GPU:0
Variable_14/Adam_1/Initializer/zeros

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



It: 0, Loss: 7.025e-01
It: 100, Loss: 4.482e-02
It: 200, Loss: 4.479e-02
It: 300, Loss: 4.473e-02
It: 400, Loss: 4.479e-02
It: 500, Loss: 4.376e-02
It: 600, Loss: 4.366e-02
It: 700, Loss: 4.353e-02
It: 800, Loss: 4.348e-02
It: 900, Loss: 4.342e-02
It: 1000, Loss: 4.336e-02
It: 1100, Loss: 4.327e-02
